In [1]:
import gensim
import pandas as pd
from gensim import corpora
from gensim.parsing.preprocessing import preprocess_string, strip_tags, strip_punctuation, strip_numeric
from gensim.models import LdaModel
from gensim.parsing.preprocessing import preprocess_string
from gensim.utils import simple_preprocess
from nltk.corpus import stopwords
import os
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from collections import Counter
import re

nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/diegojimenez/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/diegojimenez/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/diegojimenez/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [2]:

def combinar_archivos_csv(ruta):
    archivos_csv = [archivo for archivo in os.listdir(ruta) if archivo.endswith('.csv')]

   
    df_combinado = pd.DataFrame()

   
    for archivo_csv in archivos_csv:
        ruta_completa = os.path.join(ruta, archivo_csv)
        df = pd.read_csv(ruta_completa)
        df_combinado = pd.concat([df_combinado, df], ignore_index=True)

    return df_combinado


directorio = '/Users/diegojimenez/Documents/GitHub/computational_ds/data/output'


df_final = combinar_archivos_csv(directorio)


print(df_final)


           ID                                           Headline  \
0           1    5 Financial Resolutions to Start 2019 Off Right   
1           2  This Dividend-Paying Tech Stock Could Get Stro...   
2           3  German man drives into crowds; multiple injuri...   
3           4  Female Beverly Hills police chief accused of r...   
4           5  The Latest: Manchester police quiz alleged kni...   
...       ...                                                ...   
494847  37759  Huawei’s sales grew in 2019, but it says next ...   
494848  37760  The suspect in the NY Hanukkah stabbings now f...   
494849  37761  10 petitions that made the biggest impact this...   
494850  37762  A proxy war between the US and Iran just moved...   
494851  37763  Illinois governor pardons more than 11,000 peo...   

                                                Date  \
0                                                NaN   
1                                                NaN   
2              

In [3]:

text=df_final["Text"].tolist()
stop_words = set(stopwords.words('english'))

def preprocess_text(list_text, custom_stopwords):
    clean_text = []
    lemmatizer = WordNetLemmatizer()

    for text in list_text:
        if not isinstance(text, str):
            continue

        text = text.lower()
        tokens = word_tokenize(text)
        tokens = [token for token in tokens if token not in custom_stopwords]
        tokens = [token for token in tokens if token.isalpha()]
        tokens = [token for token in tokens if not token.isdigit()]
        tokens = [lemmatizer.lemmatize(token) for token in tokens]
        tokens = [token for token in tokens if token not in stop_words]

        clean_text.append(tokens)

    return clean_text
custom_stopwords=["reuters","fox","cnn"]
clean_text=preprocess_text(text, custom_stopwords)
with open('cleaned_text.txt', 'w', encoding='utf-8') as file:
    for tokens in clean_text:
        line = ' '.join(tokens)
        file.write(line + '\n')

print("Cleaned text has been saved to 'cleaned_text.txt'")


Cleaned text has been saved to 'cleaned_text.txt'


In [4]:
word_to_check = "routers"

# Check if the word is present in any sublist
found = any(word_to_check in sublist for sublist in clean_text)

if found:
    print(f"{word_to_check} is in the list.")
else:
    print(f"{word_to_check} is not in the list.")


routers is not in the list.


In [5]:
clean_text

[['many',
  'u',
  'thing',
  'year',
  'year',
  'resolve',
  'get',
  'better',
  'money',
  'matter',
  'improve',
  'couple',
  'week',
  'maybe',
  'even',
  'month',
  'let',
  'good',
  'habit',
  'lapse',
  'much',
  'colossal',
  'perhaps',
  'universal',
  'failure',
  'rate',
  'new',
  'year',
  'resolution',
  'traced',
  'back',
  'setting',
  'unrealistic',
  'goal',
  'expectation',
  'mind',
  'reasonable',
  'financial',
  'promise',
  'might',
  'likely',
  'keep',
  'start',
  'budgetingonly',
  'american',
  'household',
  'follow',
  'budget',
  'despite',
  'fact',
  'one',
  'effective',
  'money',
  'management',
  'tool',
  'resistance',
  'good',
  'american',
  'feel',
  'budgeting',
  'much',
  'work',
  'reality',
  'doe',
  'take',
  'much',
  'hour',
  'set',
  'budget',
  'another',
  'minute',
  'month',
  'revisit',
  'budget',
  'mean',
  'listing',
  'recurring',
  'monthly',
  'expense',
  'factoring',
  'expense',
  'annual',
  'membership',
  'fe

In [6]:
# Create a dictionary from the documents
#news = df_2014["text_clean"].tolist()
dictionary = corpora.Dictionary(clean_text)
# Create a corpus from the documents
corpus = [dictionary.doc2bow(doc) for doc in clean_text]

In [7]:
lda_model = LdaModel(corpus, num_topics=6, id2word=dictionary, passes=5)

In [8]:
import pyLDAvis
import pyLDAvis.gensim_models

pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda_model, corpus, dictionary)
pyLDAvis.display(vis)